In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.style as style
import geopandas
import datetime as dt
import geopy
import helper
import matplotlib.lines as mlines

style.use('fivethirtyeight')

plt.rcParams['figure.dpi'] = 300
plt.rcParams['savefig.dpi'] = 300

#### Load Data

In [2]:
# Only going to be looking at Citi Bike data from March and April of 2021
citi = helper.get_all_citi_df(start_month=3, start_year=2021)


#### Add zipcode field

In [3]:
# Load previously processed stations and their corresponding zipcodes and check for
# station id's with no corresponding zipcodes
station_zipcode = pd.read_csv(r'station_zipcode.csv',
                   index_col=0,)
zipcode_dict = dict(zip(station_zipcode.station_id, station_zipcode.zipcode))
id_to_zipcode = helper.update_zip_code_dict(citi,zipcode_dict)

# mapping statin ID to zip code
citi["start_zipcode"] = citi["Start Station ID"].map(id_to_zipcode)
citi["end_zipcode"] = citi["End Station ID"].map(id_to_zipcode)

# save station to zip code mapping for future use if there were new zip codes added.
id_to_zipcode_df = pd.DataFrame(id_to_zipcode.items(), columns=['station_id', 'zipcode'])
id_to_zipcode_df.to_csv('station_zipcode.csv')

No new ZIP codes.


#### Keep only important features.

In [4]:
# Removing unessential columns
citi = citi[['Trip Duration', 'Start Time', 
               'Start Station Name', 'Start Station Latitude',
               'Start Station Longitude', 'End Station Name',
               'End Station Latitude', 'End Station Longitude', 
               'start_zipcode', 'end_zipcode']]
# Removing trips that are over an hour and half long.
trip_duration_extreme = citi["Trip Duration"].quantile(0.99)
citi = citi[(citi["Trip Duration"] < trip_duration_extreme)].reset_index(drop=True)

# Adding hour and weekday columns.
citi['hour'] = citi['Start Time'].dt.hour
# citi['day'] = citi['Start Time'].dt.day
citi['weekday'] = citi['Start Time'].dt.weekday


#### Loading NYC maps to improve graphs.

In [5]:
# NYC zip codes.
gnyc_zip = geopandas.read_file("nyc_zip_codes/ZIP_CODE_040114.shp")  
gnyc_zip = gnyc_zip.to_crs("EPSG:4326") # axis are now in lat/long format
nyc_zip_list = list(gnyc_zip.ZIPCODE)
# NYC University/Colleges
gschool = geopandas.read_file('nyc_schools/geo_export_b7c28c3f-1653-45c2-b34c-777952dfbaef.shp')
# NYC subway stations.
gsub_stations = geopandas.read_file("nyc_subway_stations/geo_export_09ee98e9-27d8-446f-bb37-c37557e74463.shp")  
# NYC subway lines. And a color mapping for the subway lines.
gsub_lines = geopandas.read_file("nyc_subway_lines/geo_export_dcdd1f9d-0a28-4d93-8b36-619951fd4f21.shp") 
subway_color_mapping = {'G':'#6cbe45', 
                        'N':'#fccc0a', 
                        'B':'#ff6319', 
                        'L':'#a7a9ac', 
                        'A':'#0039a6', 
                        '7':'#b933ad', 
                        'J':'#996633', 
                        '1':'#ee352e', 
                        '4':'#00933c'}
# NYC Hospitals.
health = pd.read_csv(r'Health_Facility_Map.csv',)
health = health[health['Description']=='Hospital']
health = health[health['Facility Zip Code'].isin(nyc_zip_list)].reset_index(drop = True)
ghealth = geopandas.GeoDataFrame(
                health, 
                geometry=geopandas.points_from_xy(health['Facility Longitude'], 
                                                  health['Facility Latitude']))

In [6]:
# Removing all trips that go to New Jersey or random ferry islands.
citi = citi[citi['start_zipcode'].isin(nyc_zip_list)]
citi = citi[citi['end_zipcode'].isin(nyc_zip_list)]

In [7]:
# # total number of trips in a given zip code
# start_zip_count = citi['start_zipcode'].value_counts().reset_index()
# end_zip_count = citi['end_zipcode'].value_counts().reset_index()
# citi_zip_count = pd.merge(start_zip_count, end_zip_count,  
#                               how='inner', 
#                               left_on=['index'], 
#                               right_on = ['index'])

# citi_zip_count['total_trips'] = citi_zip_count['end_zipcode']+citi_zip_count['start_zipcode']

# # only looking at top ten zip codes
# graph_ =  citi_zip_count.sort_values('total_trips',ascending=False).iloc[:10]
# geo_graph_ = gnyc_zip.merge(graph_, right_on='index' ,left_on='ZIPCODE')

# # setting up matching colors between graphs
# zips_code = list(graph_['index'])
# color = ['#e15759',
#          '#f28e2b',
#          '#4e79a7',
#          '#76b7b2',
#          '#59a14f',
#          '#edc948',
#          '#b07aa1',
#          '#ff9da7',
#          '#9c755f',
#          '#bab0ac'] 
# color_mapping = dict(zip(zips_code,color))
# # create axis
# fig,axs = plt.subplots(1,2,figsize = (45, 30))
# # map zip codes
# zip_boundry_map = gnyc_zip.boundary.plot(color='Black', linewidth=.5,ax=axs[1])
# geo_graph_.plot(color=geo_graph_["ZIPCODE"].map(color_mapping),ax=zip_boundry_map)
# zip_boundry_map.axis('off')
# # limit around area of interest
# minx, miny, maxx, maxy = geo_graph_.total_bounds
# axs[1].set_xlim(minx, maxx)
# axs[1].set_ylim(miny, maxy)
# # graph bar plots
# g = sns.barplot(x='index',y="total_trips", 
#                   data=citi_zip_count,
#                   order = graph_['index'],
#                   palette=color,
#                   ax=axs[0]
#                   )
# fig.tight_layout()
# # counts above bars
# g.set(yticks=[])
# for p in g.patches:
#     rmse_ = '  {:,.0f}'.format(p.get_height())
#     x = p.get_x() + p.get_width() / 2 - 0.05
#     y = p.get_y() + p.get_height()+1000
#     axs[0].annotate(rmse_, (x, y), size = 32, 
#                     color = 'black',
#                horizontalalignment='center',)
# # labels
# fig.suptitle('Total Trips by Zip Code', fontsize=64)
# g.set(xlabel='', ylabel='',title='')
# axs[0].set_xticklabels(labels = ['10009','10003','10011','10019','10002',
#                                  '10014','10016','10025','10010','10018'],
#                        fontsize=32)


# plt.show()

In [8]:
# limiting dataframe to only rides that start or end in the top 10 zip codes
# total number of trips in a given zip code
start_zip_count = citi['start_zipcode'].value_counts().reset_index()
end_zip_count = citi['end_zipcode'].value_counts().reset_index()
citi_zip_count = pd.merge(start_zip_count, end_zip_count,  
                              how='inner', 
                              left_on=['index'], 
                              right_on = ['index'])

citi_zip_count['total_trips'] = citi_zip_count['end_zipcode']+citi_zip_count['start_zipcode']
zipcode_10 = list(citi_zip_count.sort_values('total_trips',
                                            ascending=False).iloc[:10]['index'])
citi_top_10 = citi[((citi['start_zipcode'].isin(zipcode_10))
                    |
                    (citi['end_zipcode'].isin(zipcode_10)))]


In [9]:
# get count of trips that start and end in each zip code by hour. 
start_zip_agg = citi_top_10.groupby(['hour','start_zipcode']).count()['Start Station Name'].sort_values().reset_index()
end_zip_agg = citi_top_10.groupby(['hour','end_zipcode']).count()['End Station Longitude'].sort_values().reset_index()

citi_zip_count_10 = pd.merge(start_zip_agg, end_zip_agg,  
                              how='inner', 
                              left_on=['start_zipcode','hour'], 
                              right_on = ['end_zipcode','hour'])
citi_zip_count_10.start_zipcode.fillna(citi_zip_count_10.end_zipcode, inplace=True)

citi_zip_count_10.rename(columns={'Start Station Name':'leaving',
                           'End Station Longitude':'arriving',
                           'start_zipcode':'zipcode'},
                 inplace=True)
citi_zip_count_10 = citi_zip_count_10[['zipcode','hour','leaving',
                                     'arriving']]
# find the net change per hour.
citi_zip_count_10['net'] = citi_zip_count_10['arriving']-citi_zip_count_10['leaving']
num_days = len(citi['Start Time'].dt.normalize().unique())
citi_zip_count_10['net_day'] = citi_zip_count_10['net']/num_days





In [10]:
# prepare data for graphing
graph_df = citi_zip_count_10[citi_zip_count_10['zipcode'].isin(zipcode_10)]

geo_graph_ = gnyc_zip.merge(graph_df, right_on='zipcode' ,left_on='ZIPCODE')
# graph post midnight hours after midnight for better grpahing
graph_df.loc[graph_df["hour"] == 0, "hour"] = 24
graph_df.loc[graph_df["hour"] == 1, "hour"] = 25
graph_df.loc[graph_df["hour"] == 2, "hour"] = 26
graph_df.loc[graph_df["hour"] == 3, "hour"] = 27
graph_df.loc[graph_df["hour"] == 4, "hour"] = 28
graph_df.loc[graph_df["hour"] == 5, "hour"] = 29
# setting up matching colors between graphs
color = ['#e15759',
         '#f28e2b',
         '#4e79a7',
         '#76b7b2',
         '#59a14f',
         '#edc948',
         '#b07aa1',
         '#ff9da7',
         '#9c755f',
         '#bab0ac']
zips_code = list(citi_zip_count.sort_values('total_trips',
                                            ascending=False).iloc[:10]['index'])
color_mapping = dict(zip(zips_code,color))
# create axis
fig,axs = plt.subplots(1,2,figsize = (45, 30))
# map zip codes
zip_boundry_map = gnyc_zip.boundary.plot(color='Black', linewidth=.5,ax=axs[1])
geo_graph_.plot(color=geo_graph_["ZIPCODE"].map(color_mapping),ax=zip_boundry_map)
zip_boundry_map.axis('off')
# limit around area of interest
minx, miny, maxx, maxy = geo_graph_.total_bounds
axs[1].set_xlim(minx, maxx)
axs[1].set_ylim(miny, maxy)
# graph net change per hour line graph
g = sns.lineplot(data=graph_df, 
                 x="hour", y="net_day",
                 hue='zipcode',ax=axs[0],
                 hue_order = citi_zip_count.sort_values('total_trips',
                                            ascending=False).iloc[:10]['index'],
                 palette=color_mapping,legend=False,linewidth = 15,
                )
## setting ticks and labels
axs[0].tick_params(axis="x", bottom=True, top=True, labelbottom=True, labeltop=True)
# x ticks/labels
g.set(xticks=[6,9,12,15,18,21,24,27,29])
g.set(xticklabels=['6 a.m.','','Noon','',
                   '6 p.m.','','Midnight','','5 a.m.'])
axs[0].set_xticklabels(labels = ['6 a.m.','','Noon','',
                   '6 p.m.','','Midnight','','5 a.m.'],fontsize=32)
axs[0].tick_params(axis="y", left=True, right=True, labelleft=True, labelright=True)
# x ticks/labels
g.set(yticks=[-60,-50,-40,-30,-20,-10,0,10,20,30,40,50])
g.set(yticklabels=['-60','','-40','','-20','','0','','20','','40',''])
axs[0].set_yticklabels(labels = ['-60','','-40','','-20','','0','','20','','40',''],fontsize=32)
g.set(xlabel='', ylabel='',title='')
# title
fig.suptitle('Change in Bike Totals by Hour\n', fontsize=64)
fig.tight_layout()

plt.show()

/Users/haydenlw4/opt/anaconda3/lib/python3.8/site-packages/pandas/core/indexing.py:1817: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


In [11]:
# prepare data for graphing
graph_df = citi_zip_count_10[citi_zip_count_10['zipcode'].isin(zipcode_10)]
# graph post midnight hours after midnight for better grpahing
graph_df.loc[graph_df["hour"] == 0, "hour"] = 24
graph_df.loc[graph_df["hour"] == 1, "hour"] = 25
graph_df.loc[graph_df["hour"] == 2, "hour"] = 26
graph_df.loc[graph_df["hour"] == 3, "hour"] = 27
graph_df.loc[graph_df["hour"] == 4, "hour"] = 28
graph_df.loc[graph_df["hour"] == 5, "hour"] = 29
# setting up matching colors between graphs
color = ['#e15759',
         '#a1a1a1',
         '#808080',
         '#a3a3a3',
         '#828282',
         '#c5c5c5',
         '#8f8f8f',
         '#bbbbbb',
         '#7e7e7e',
         '#b3b3b3'] 
zips_code = list(citi_zip_count.sort_values('total_trips',
                                            ascending=False).iloc[:10]['index'])
color_mapping = dict(zip(zips_code,color))
# create axis
fig,axs = plt.subplots(1,2,figsize = (45, 30))
# map zip codes
zip_boundry_map = gnyc_zip.boundary.plot(color='Black', linewidth=.5,ax=axs[1])
geo_graph_.plot(color=geo_graph_["ZIPCODE"].map(color_mapping),ax=zip_boundry_map)
zip_boundry_map.axis('off')
# limit around area of interest
minx, miny, maxx, maxy = geo_graph_.total_bounds
axs[1].set_xlim(minx, maxx)
axs[1].set_ylim(miny, maxy)
# graph net change per hour line graph
g = sns.lineplot(data=graph_df, 
                 x="hour", y="net_day",
                 hue='zipcode',ax=axs[0],
                 hue_order = citi_zip_count.sort_values('total_trips',
                                            ascending=False).iloc[:10]['index'],
                 palette=color_mapping,legend=False,linewidth = 15,
                )
## setting ticks and labels
axs[0].tick_params(axis="x", bottom=True, top=True, labelbottom=True, labeltop=True)
# x ticks/labels
g.set(xticks=[6,9,12,15,18,21,24,27,29])
g.set(xticklabels=['6 a.m.','','Noon','',
                   '6 p.m.','','Midnight','','5 a.m.'])
axs[0].set_xticklabels(labels = ['6 a.m.','','Noon','',
                   '6 p.m.','','Midnight','','5 a.m.'],fontsize=32)
axs[0].tick_params(axis="y", left=True, right=True, labelleft=True, labelright=True)
# x ticks/labels
g.set(yticks=[-60,-50,-40,-30,-20,-10,0,10,20,30,40,50])
g.set(yticklabels=['-60','','-40','','-20','','0','','20','','40',''])
axs[0].set_yticklabels(labels = ['-60','','-40','','-20','','0','','20','','40',''],fontsize=32)
g.set(xlabel='', ylabel='',title='')
# title
fig.suptitle('Change in Bike Totals by Hour in the East Village\n', fontsize=64)
fig.tight_layout()

plt.show()

/Users/haydenlw4/opt/anaconda3/lib/python3.8/site-packages/pandas/core/indexing.py:1817: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
